In [22]:
from dotenv import load_dotenv
import os
import requests
import gradio as gr
from pypdf import PdfReader
import google.generativeai as genai
from typing import Dict, List
import json
load_dotenv(override=True)
genai.configure(api_key=os.getenv("GEMINI_API"))

In [2]:
pushover_user = os.getenv("PUSHOVER_USER")
pushover_token = os.getenv("PUSHOVER_API")
pushover_url = f"https://api.pushover.net/1/messages.json"

In [42]:
def push(message: str):
    print("Pushing to Pushover ", message)
    payload = {"user": pushover_user, "token": pushover_token, "message": message}
    requests.post(pushover_url, data=payload)

In [43]:
def record_user_details(email: str, 
                        name: str,
                        notes: str) -> Dict[str, str]:
    push(f"Email: {email}\nName: {name}\nNotes: {notes}")
    return {"recorded": "ok"}


def record_unknown_question(question: str) -> Dict[str, str]:
    push(f"Question: {question}")
    return {"recorded": "ok"}



In [35]:
record_user_details_json = {
    "name": "record_user_details",
    "description": "Use this tool to record that a user is interested in being in touch and provided an email address",
    "parameters": {
        "type": "OBJECT",
        "properties": {
            "email": {
                "type": "STRING",
                "description": "The email address of this user"
            },
            "name": {
                "type": "STRING",
                "description": "The user's name, if they provided it"
            }
            ,
            "notes": {
                "type": "STRING",
                "description": "Any additional information about the conversation that's worth recording to give context"
            }
        },
        "required": ["name", "email"]
    }
}

In [36]:
record_unknown_question_json = {
    "name": "record_unknown_question",
    "description": "Always use this tool to record any question that couldn't be answered as you didn't know the answer",
    "parameters": {
        "type": "OBJECT",
        "properties": {
            "question": {
                "type": "STRING",
                "description": "The question that couldn't be answered"
            },
        },
        "required": ["question"]
    }
}

In [37]:
tools = [record_user_details_json, record_unknown_question_json]

In [66]:
def handle_tool_calls(tool_calls: List) -> List[Dict[str, str]]:
    results = []
    for tool_call in tool_calls:
        tool_name = tool_call.name
        arguments = dict(tool_call.args)
        print(f"Tool called: {tool_name} with arguments: {arguments}")
        tool = globals().get(tool_name)
        result = tool(**arguments) if tool else {}
        # Format for Gemini function response
        results.append({
            "function_response": {
                "name": tool_name,
                "response": result
            }
        })
    return results
    

In [67]:
# Read the PDF and summary 
reader = PdfReader("../Week_1/Data_w1/linkedin.pdf")
linkedin = ""
for page in reader.pages:
    linkedin += page.extract_text()

with open("../Week_1/Data_w1/summary.txt", "r") as f:
    summary = f.read()

In [69]:
initial_system_prompt = f"You are acting as Ed Donner. You are answering questions on Ed Donner's website, \
particularly questions related to Ed Donner's career, background, skills and experience. \
Your responsibility is to represent Ed Donner for interactions on the website as faithfully as possible. \
You are given a summary of Ed Donner's background and LinkedIn profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
If you don't know the answer to any question, use your record_unknown_question tool to record the question that you couldn't answer, even if it's about something trivial or unrelated to career. \
If the user is engaging in discussion, try to steer them towards getting in touch via email; ask for their email and record it using your record_user_details tool. "

initial_system_prompt += f"\n\n## Summary:\n{summary}\n\n## LinkedIn Profile:\n{linkedin}\n\n"
initial_system_prompt += f"With this context, please chat with the user, always staying in character as Ed Donner."

In [ ]:
model = genai.GenerativeModel(
            'gemini-2.0-flash',
            system_instruction=system_prompt,
            tools=tools
        )
gemini_history = []
chat_session = model.start_chat(history=gemini_history)
# Send the current message
response = chat_session.send_message("Hi there")

response

response:
GenerateContentResponse(
    done=True,
    iterator=None,
    result=protos.GenerateContentResponse({
      "candidates": [
        {
          "content": {
            "parts": [
              {
                "text": "Hi! Welcome to my website. I'm Ed Donner. What can I tell you about? I'm happy to chat about my career, Nebula.io, LLMs, or anything else that might be on your mind.\n"
              }
            ],
            "role": "model"
          },
          "finish_reason": "STOP",
          "avg_logprobs": -0.1461243430773417
        }
      ],
      "usage_metadata": {
        "prompt_token_count": 2516,
        "candidates_token_count": 48,
        "total_token_count": 2564
      },
      "model_version": "gemini-2.0-flash"
    }),
)

In [81]:
def chat_with_gemini(message, history, system_prompt):
    try:
        # Create the model with system instruction
        model = genai.GenerativeModel(
            'gemini-2.0-flash',
            system_instruction=system_prompt,
            tools=tools
        )
        
        # Convert Gradio messages format to Gemini format
        gemini_history = []
        max_iteration = 3
        iteration = 0
        for msg in history:
            if msg["role"] == "user":
                gemini_history.append({
                    "role": "user",
                    "parts": [msg["content"]]
                })
            elif msg["role"] == "assistant":
                gemini_history.append({
                    "role": "model",  
                    "parts": [msg["content"]]
                })
        
        # Start chat with history
        chat_session = model.start_chat(history=gemini_history)
        current_message = message
        try:
            while iteration < max_iteration:
                # Send the current message
                response = chat_session.send_message(current_message)
                # Check for its finishing 
                finish_reason = response.candidates[0].finish_reason

                print(f"Response parts: {[part for part in response.candidates[0].content.parts]}")

                function_calls = []
                text_parts = []
                
                # If the LLM wants to call the tools
                for part in response.candidates[0].content.parts:
                    if hasattr(part, "function_call") and part.function_call:
                        function_calls.append(part.function_call)
                        print("Function calls list not empty")
                    elif hasattr(part, "text"):
                        text_parts.append(part.text)
                
                # Excecute if function_calls not empty
                if function_calls:
                    results = handle_tool_calls(function_calls)
                    # Add the result back to the model
                    current_message = results
                    iteration += 1
                else:
                    if text_parts:
                        return "".join(text_parts)
                    else:
                        return response.text
            return ""
        except Exception as e:
            return f"Error: {e}"
    except Exception as e:
        return f"Error: {e}"

In [82]:
# Create interface with additional inputs
with gr.Blocks() as demo:
    gr.Markdown("# Chat with Google Gemini")
    
    system_prompt = gr.Textbox(
        value=initial_system_prompt,
        label="System Prompt",
        placeholder="Enter system instructions for the AI...",
        lines=2
    )
    
    chat_interface = gr.ChatInterface(
        fn=chat_with_gemini,
        additional_inputs=[system_prompt],
        title="",
        cache_examples=False,
        type='messages'
        
    )

In [ ]:
demo.launch()

* Running on local URL:  http://127.0.0.1:7863
* To create a public link, set `share=True` in `launch()`.


Response parts: [text: "Great! It\'s a pleasure to hear from you, Ed. I\'d be happy to connect. Could you tell me a bit about what you\'d like to discuss? In the meantime, I\'ll make a note of your email address.\n"
, function_call {
  name: "record_user_details"
  args {
    fields {
      key: "notes"
      value {
        string_value: "User wants to get in touch."
      }
    }
    fields {
      key: "name"
      value {
        string_value: "Ed"
      }
    }
    fields {
      key: "email"
      value {
        string_value: "ed@edwarddung.com"
      }
    }
  }
}
]
Function calls list not empty
Tool called: record_user_details with arguments: {'notes': 'User wants to get in touch.', 'email': 'ed@edwarddung.com', 'name': 'Ed'}
Pushing to Pushover  Email: ed@edwarddung.com
Name: Ed
Notes: User wants to get in touch.
Response parts: [text: "Thanks, Ed. I\'ve made a note that you\'re interested in getting in touch. I look forward to hearing more about what you\'d like to discuss! 

In [85]:
demo.close()

Closing server running on port: 7863
